In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import os
from dotenv import load_dotenv

# Import dataset

In [ ]:
# Chargement API KEYS
load_dotenv()

API_KEY_S3 = os.environ["API_KEY_S3"]
API_SECRET_KEY_S3 = os.environ["API_SECRET_KEY_S3"]

bucket_name = "renergies99-lead-bucket"
s3_prefix = "public"

In [ ]:
df = pd.read_csv(
    "s3://renergies99-lead-bucket/public/prod/eCO2mix_RTE_Auvergne-Rhone-Alpes.csv",
    storage_options={
        "key": API_KEY_S3,
        "secret": API_SECRET_KEY_S3,
    }
)

C:\Users\jean-\AppData\Local\Temp\ipykernel_8400\2214913187.py:1: DtypeWarning: Columns (12,13,14,15,18,20,25,26,28,30,32,37,38,40,44,47,51,54) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(


In [4]:
df.head()

Périmètre              Nature        Date    Heures  \
0  Auvergne-Rhône-Alpes  Données temps réel  2025-01-01  00:00:00   
1  Auvergne-Rhône-Alpes  Données temps réel  2025-01-01  00:30:00   
2  Auvergne-Rhône-Alpes  Données temps réel  2025-01-01  01:00:00   
3  Auvergne-Rhône-Alpes  Données temps réel  2025-01-01  01:30:00   
4  Auvergne-Rhône-Alpes  Données temps réel  2025-01-01  02:00:00   

   Consommation  Thermique  Nucléaire  Eolien  Solaire  Hydraulique  ...  \
0        9002.0      134.0    11017.0   118.0      0.0       2609.0  ...   
1        8940.0      133.0    10733.0   137.0      0.0       2454.0  ...   
2        8802.0      126.0    10137.0   151.0      0.0       2319.0  ...   
3        8718.0      125.0     9573.0   154.0      0.0       2511.0  ...   
4        8719.0      126.0     9603.0   164.0      0.0       2500.0  ...   

   TCO Nucléaire (%)  TCH Nucléaire (%) TCO Eolien (%) TCH Eolien (%)  \
0             122.38              81.19           1.31          15.92   
1             120.06              79.09           1.53          18.49   
2             115.17              74.70           1.72          20.38   
3             109.81              70.55           1.77          20.78   
4             110.14              70.77           1.88          22.13   

  TCO Solaire (%) TCH Solaire (%)  TCO Hydraulique (%) TCH Hydraulique (%)  \
0             0.0             0.0                28.98               22.88   
1             0.0             0.0                27.45               21.52   
2             0.0             0.0                26.35               20.34   
3             0.0             0.0                28.80               22.02   
4             0.0             0.0                28.67               21.93   

  TCO Bioénergies (%) TCH Bioénergies (%)  
0                0.44               21.16  
1                0.45               21.16  
2                0.45               21.16  
3                0.46               21.16  
4                0.46               21.16  

[5 rows x 67 columns]

In [5]:
df.shape

(85514, 67)

In [6]:
print(df.info())
print(df.describe())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 85514 entries, 0 to 85513
Data columns (total 67 columns):
 #   Column                                                               Non-Null Count  Dtype  
---  ------                                                               --------------  -----  
 0   Périmètre                                                            85514 non-null  object 
 1   Nature                                                               85510 non-null  object 
 2   Date                                                                 85510 non-null  object 
 3   Heures                                                               85510 non-null  object 
 4   Consommation                                                         85510 non-null  float64
 5   Thermique                                                            85510 non-null  float64
 6   Nucléaire                                                            85510 non-null  float64
 7   Eoli

# EDA

## Analyse temporelle

In [7]:
df['datetime'] = pd.to_datetime(df['Date'] + ' ' + df['Heures'], errors='coerce')
df = df.sort_values('datetime')

df['year'] = df['datetime'].dt.year
df['month'] = df['datetime'].dt.month
df['day'] = df['datetime'].dt.day
df['hour'] = df['datetime'].dt.hour
df['weekday'] = df['datetime'].dt.day_name(locale='fr_FR')

jours_fr = ["Lundi","Mardi","Mercredi","Jeudi","Vendredi","Samedi","Dimanche"]
df["weekday_num"] = df["datetime"].dt.dayofweek
df["weekday_fr"] = df["weekday_num"].map(dict(enumerate(jours_fr)))
df["is_weekend"] = df["weekday_fr"].isin(["Samedi","Dimanche"])

In [8]:
# Évolution de la consommation dans le temps
df_daily = (
    df.dropna(subset=["Date","Consommation"])
      .groupby("Date", as_index=False)["Consommation"].mean()
)
df_daily["Date"] = pd.to_datetime(df_daily["Date"], errors="coerce")
fig1 = px.line(df_daily, x="Date", y="Consommation",
               title="Consommation moyenne quotidienne")
fig1.show()

In [9]:
# Saisonnalité horaire
df_hour = (
    df.dropna(subset=["hour","Consommation"])
      .groupby("hour", as_index=False)["Consommation"].mean()
)
fig2 = px.bar(df_hour, x="hour", y="Consommation",
              title="Consommation moyenne par heure de la journée")
fig2.show()

In [10]:
# Saisonnalité mensuelle
df_month = (
    df.dropna(subset=["month","Consommation"])
      .groupby("month", as_index=False)["Consommation"].mean()
)
fig3 = px.bar(df_month, x="month", y="Consommation",
              title="Consommation moyenne par mois")
fig3.show()

In [11]:
# Semaine vs week-end
df_week = (
    df.dropna(subset=["is_weekend","Consommation"])
      .groupby("is_weekend", as_index=False)["Consommation"].mean()
      .replace({"is_weekend": {True: "Week-end", False: "Semaine"}})
)
fig4 = px.bar(df_week, x="is_weekend", y="Consommation",
              title="Consommation moyenne : semaine vs week-end")
fig4.show()

In [12]:
# Évolution des productions principales non revouvlable (Nucléaire)
prod_cols_01 = [c for c in ["Nucléaire"]
             if c in df.columns]
if prod_cols_01:
    df_prod = (
        df.dropna(subset=["Date"])
          .groupby("Date", as_index=False)[prod_cols_01].mean()
    )
    df_prod["Date"] = pd.to_datetime(df_prod["Date"], errors="coerce")
    df_prod_long = df_prod.melt(id_vars="Date", value_vars=prod_cols_01,
                                var_name="source", value_name="production_MW")
    fig5 = px.line(df_prod_long, x="Date", y="production_MW", color="source",
                   title="Évolution moyenne journalière des productions par source")
    fig5.show()


In [13]:
# Évolution des productions principales renouvelables
prod_cols_02 = [c for c in ["Eolien", "Solaire", "Hydraulique"]
             if c in df.columns]
if prod_cols_02:
    df_prod = (
        df.dropna(subset=["Date"])
          .groupby("Date", as_index=False)[prod_cols_02].mean()
    )
    df_prod["Date"] = pd.to_datetime(df_prod["Date"], errors="coerce")
    df_prod_long = df_prod.melt(id_vars="Date", value_vars=prod_cols_02,
                                var_name="source", value_name="production_MW")
    fig6 = px.line(df_prod_long, x="Date", y="production_MW", color="source",
                   title="Évolution moyenne journalière des productions par source")
    fig6.show()

In [14]:
# moyenne par jour de semaine et par heure (heatmap)
pivot = (df.dropna(subset=["weekday_fr","hour","Consommation"])
           .groupby(["weekday_fr","hour"], as_index=False)["Consommation"].mean())
pivot["weekday_fr"] = pd.Categorical(pivot["weekday_fr"], categories=jours_fr, ordered=True)
pivot = pivot.sort_values(["weekday_fr","hour"])

fig8 = px.density_heatmap(pivot, x="hour", y="weekday_fr", z="Consommation",
                          nbinsx=24, histfunc="avg",
                          title="Consommation moyenne par heure et jour de semaine")
fig8.show()

## Analyse énergétique

In [15]:
# Composition du mix énergétique global
prod_cols = [c for c in [
    "Nucléaire", "Gaz", "Charbon", "Fioul",
    "Hydraulique", "Eolien", "Solaire", "Bioénergies"
] if c in df.columns]

df["production_totale"] = df[prod_cols].sum(axis=1)

mix_global = (
    df[prod_cols]
    .mean()
    .sort_values(ascending=False)
    .rename_axis("source")
    .reset_index(name="production_moyenne")
)

fig1 = px.pie(
    mix_global,
    names="source",
    values="production_moyenne",
    title="Répartition moyenne du mix énergétique",
    hole=0.4,
    color="source"
)

fig1.update_traces(
    textposition="inside",
    textinfo="percent+label",
    hovertemplate="<b>%{label}</b><br>" +
                  "Part: %{percent:.1%}<br>" +
                  "Prod. moyenne: %{value:.0f} MW<extra></extra>"
)

fig1.update_layout(
    legend_title_text="Filière",
    margin=dict(t=80, l=0, r=0, b=20)
)

fig1.show()

In [16]:
# Moyenne de production par source (par heure)
df_hour_prod = (
    df.groupby("hour")[prod_cols]
    .mean()
    .reset_index()
    .melt(id_vars="hour", var_name="source", value_name="production_moyenne")
)

fig6 = px.line(
    df_hour_prod,
    x="hour",
    y="production_moyenne",
    color="source",
    title="Profil moyen horaire de production par source"
)
fig6.show()

## Analyse des échanges inter régions

- Valeur positive → import net
- Valeur négative → export net

In [17]:
df.filter(like="Ech").columns

Index(['Ech. physiques'], dtype='object')

In [18]:
# Flux physiques globaux
solde = df["Ech. physiques"]

print("Moyenne :", solde.mean())
print("Min (export max):", solde.min())
print("Max (import max):", solde.max())

Moyenne : -5487.943468600164
Min (export max): -12787.0
Max (import max): 1270.0


In [19]:
# Evolution du solde dans le temps
fig = px.line(
    df,
    x="Date",
    y="Ech. physiques",
    title="Solde global des échanges physiques (import + / export -)",
)
fig.add_hline(y=0, line_dash="dash")

fig.show()

In [20]:
# Exports
export_cols = [col for col in df.columns if "vers" in col and "Auvergne" not in col]
export_cols = [
    col for col in df.columns 
    if col.startswith("Flux physiques de Auvergne-Rhône-Alpes vers")
]
export_cols

['Flux physiques de Auvergne-Rhône-Alpes vers Auvergne-Rhône-Alpes',
 'Flux physiques de Auvergne-Rhône-Alpes vers Bourgogne-Franche-Comté',
 'Flux physiques de Auvergne-Rhône-Alpes vers Bretagne',
 'Flux physiques de Auvergne-Rhône-Alpes vers Centre-Val de Loire',
 'Flux physiques de Auvergne-Rhône-Alpes vers Grand-Est',
 'Flux physiques de Auvergne-Rhône-Alpes vers Hauts-de-France',
 'Flux physiques de Auvergne-Rhône-Alpes vers Ile-de-France',
 'Flux physiques de Auvergne-Rhône-Alpes vers Normandie',
 'Flux physiques de Auvergne-Rhône-Alpes vers Nouvelle-Aquitaine',
 'Flux physiques de Auvergne-Rhône-Alpes vers Occitanie',
 'Flux physiques de Auvergne-Rhône-Alpes vers Pays-de-la-Loire',
 'Flux physiques de Auvergne-Rhône-Alpes vers PACA',
 'Flux physiques de Auvergne-Rhône-Alpes vers Allemagne',
 'Flux physiques de Auvergne-Rhône-Alpes vers Belgique',
 'Flux physiques de Auvergne-Rhône-Alpes vers Espagne',
 'Flux physiques de Auvergne-Rhône-Alpes vers Italie',
 'Flux physiques de Auv

In [21]:
export_numeric = df[export_cols].apply(pd.to_numeric, errors="coerce")
export_sum = export_numeric.sum().sort_values(ascending=False)
export_sum

Flux physiques de Auvergne-Rhône-Alpes vers Occitanie                  169230472.0
Flux physiques de Auvergne-Rhône-Alpes vers Italie                      46814946.0
Flux physiques de Auvergne-Rhône-Alpes vers Bourgogne-Franche-Comté     25084638.0
Flux physiques de Auvergne-Rhône-Alpes vers Suisse                      20958424.0
Flux physiques de Auvergne-Rhône-Alpes vers PACA                        17933853.0
Flux physiques de Auvergne-Rhône-Alpes vers Centre-Val de Loire          5382596.0
Flux physiques de Auvergne-Rhône-Alpes vers Nouvelle-Aquitaine           3427243.0
Flux physiques de Auvergne-Rhône-Alpes vers Grand-Est                          0.0
Flux physiques de Auvergne-Rhône-Alpes vers Hauts-de-France                    0.0
Flux physiques de Auvergne-Rhône-Alpes vers Ile-de-France                      0.0
Flux physiques de Auvergne-Rhône-Alpes vers Normandie                          0.0
Flux physiques de Auvergne-Rhône-Alpes vers Pays-de-la-Loire                   0.0
Flux

In [22]:
prefix = "Flux physiques de Auvergne-Rhône-Alpes vers "

export_sum_clean = export_sum.copy()
export_sum_clean.index = export_sum_clean.index.str.replace(prefix, "", regex=False)

In [23]:
export_top = export_sum_clean.sort_values(ascending=False).head(6)

In [24]:
fig = px.bar(
    x=export_top.values,
    y=export_top.index,
    orientation="h",
    title="Top des volumes exportés cumulés depuis Auvergne-Rhône-Alpes",
    labels={"x": "MW exportés", "y": "Région"}
)

fig.update_layout(
    height=500,
    yaxis=dict(categoryorder="total ascending")
)

fig.update_xaxes(tickformat=".2s")

fig.show()

## Analyse taux de couverture et charges

- TCO (Taux de Couverture) = capacité disponible / capacité max
- TCH (Taux de Charge) = production réelle / capacité disponible

### Analyse comparative

In [25]:
# TCO moyen par filière
tco_cols = {
    "Thermique": "TCO Thermique (%)",
    "Nucléaire": "TCO Nucléaire (%)",
    "Éolien": "TCO Eolien (%)",
    "Solaire": "TCO Solaire (%)",
    "Hydraulique": "TCO Hydraulique (%)",
    "Bioénergies": "TCO Bioénergies (%)"
}

# Calcul des moyennes
tco_mean = {k: df[v].mean() for k, v in tco_cols.items()}
tco_df = pd.DataFrame(list(tco_mean.items()), columns=["Filière", "TCO_moyen"])

# Bar chart
px.bar(tco_df, x="Filière", y="TCO_moyen", title="TCO moyen par filière (%)")

In [26]:
# TCH moyen par filière
tch_cols = {
    "Thermique": "TCH Thermique (%)",
    "Nucléaire": "TCH Nucléaire (%)",
    "Eolien": "TCH Eolien (%)",
    "Solaire": "TCH Solaire (%)",
    "Hydraulique": "TCH Hydraulique (%)",
    "Bioénergies": "TCH Bioénergies (%)"
}

tch_mean = {k: df[v].mean() for k, v in tch_cols.items()}
tch_df = pd.DataFrame(list(tch_mean.items()), columns=["Filière", "TCH_moyen"])

px.bar(tch_df, x="Filière", y="TCH_moyen", title="TCH moyen par filière (%)")

In [27]:
# TCH par filière et par mois
def clean_tch(col):
    return (
        col.astype(str)
        .str.replace("\u202f", "", regex=False)
        .str.replace(" ", "", regex=False)
        .str.replace(",", ".", regex=False)
        .str.replace("%", "", regex=False)
    )

for c in tch_cols:
    df[c] = clean_tch(df[c])
    df[c] = pd.to_numeric(df[c], errors="coerce")

df_long = df.melt(
    id_vars="Date",
    value_vars=tch_cols,
    var_name="Filière",
    value_name="TCH (%)"
)
df_long["Date"] = pd.to_datetime(df_long["Date"])
df_long["Mois"] = df_long["Date"].dt.to_period("M").dt.to_timestamp()

df_month = df_long.groupby(["Mois", "Filière"], as_index=False)["TCH (%)"].mean()
fig = px.line(
    df_month,
    x="Mois",
    y="TCH (%)",
    color="Filière",
    title="TCH (%) moyen par filière – vision mensuelle"
)

fig.show()